# AA-UTE 2024

## Práctica 2 - Clasificadores no paramétricos e Hiperparámetros

### Objetivos:
En esta práctica se entra en detalle en los clasificadores de `kNN` (k-vecinos más cercanos) y `árboles de decisión`. Dichos clasificadores tienen la particularidad de tener un interpretabilidad simple y son fáciles de visualizar.

También se tendrá un manejo de los `hiperparámetros` para cada modelo. A su vez, se presentan maneras de evaluar la elección de los mismos.

Para varias gráficas de la práctica se utilizan funciones auxiliares cargados desde un archivo python _utils.py_, ubicado en el mismo directorio de éste notebook.

# Imports

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.datasets import make_moons, make_classification
from sklearn.model_selection import train_test_split    
from sklearn.metrics import accuracy_score              

# kNN

In [ ]:
# Definición de gráfica para un clasificador kNN
from sklearn.neighbors import KNeighborsClassifier
from utils import plot2D_knn_results

In [ ]:
# Cantidad de muestras a usar
n_samples = 300

# Generación de datos para clasificación
X, y = make_classification(n_samples=n_samples, n_features=2, n_informative=2, 
                           n_redundant=0, n_classes=4, n_clusters_per_class=1, 
                           random_state=42, weights=[0.4, 0.2, 0.15, 0.5])

# Dividir en conjuntos train/test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [ ]:
# Visualizar conjunto de datos
plt.scatter(X[:, 0], X[:, 1], c=y, edgecolors='k')
plt.title('Espacio de características')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()

Visualizar las regiones de decisión para $k=1$ y $k=5$. Responder: 
1. ¿En qué se diferencian las regiones? 
1. ¿Cuál parece ser la correcta?

In [ ]:
# Fijar valor de k
k = 1

# Inicializar clasificador con el valor de k
clf_knn = KNeighborsClassifier(n_neighbors=k) # COMPLETAR
clf_knn.fit(X_train, y_train)

plot2D_knn_results(clf_knn, X_train, y_train, ['Feature 1','Feature 2'], ['','','',''],test_point=None)

Ver para $k=\{1,5\}$ qué vecinos deciden la clasificación en un dato del conjunto de test.

In [ ]:
# Fijar valor de k
k = 1

# Fijar índice de dato test
index = 0                                       # decomentar para usar índice fijo (ver p. ej: 0, 22, 43, 51)
# index = np.random.randint(0,len(y_test))      # descomentar para usar indice aleatorio 

clf_knn = KNeighborsClassifier(n_neighbors=k) # COMPLETAR
clf_knn.fit(X_train, y_train)

dato_test = X_test[index]

print('Predicción clase de dato test:', clf_knn.predict([X_test[index]]))

plot2D_knn_results(clf_knn, X_train, y_train, ['Feature 1','Feature 2'], ['0','1','2','3'], test_point=dato_test)

Realizar una **curva $k$ _vs_ $accuracy$**, para los conjuntos de entrenamiento y de test con los valores de $k=\{1,2,...,29,30\}$. ¿Cuál es el valor del _**hiper-parámetro**_ k que generaliza mejor?

Usar el siguiente dataset sintético.

In [ ]:
# Generar datos sintéticos
X, y = make_moons(n_samples=300, noise=0.4, random_state=42)

# Visualizar conjunto de datos
plt.scatter(X[:, 0], X[:, 1], c=y, edgecolors='k')
plt.title('Espacio de características')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()

# Split en train y test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=30)

Completar usando los valores $k=\{1,2,...,29,30\}$ y guardando el _accuracy_ en train y test para cada valor de $k$

In [ ]:
# Asignar k= 1,2,...,30 para entrenar
ks = np.arange(1,31) # COMPLETAR

# Inicializar lista para guardar valores de accuracy
ks_train_acc = np.zeros(len(ks))
ks_test_acc = np.zeros(len(ks))

# Indice para subplot
indx = 0
# Inicializar figura
plt.figure(figsize=(15,10))

# Iterar por cada valor de k
for indice, k in enumerate(ks):
    
    # Entrenar clasificador con los k vecinos 
    knn = KNeighborsClassifier(n_neighbors=k) # COMPLETAR
    knn.fit(X_train, y_train)

    # Evaluar accuracy en train y guardar
    train_accuracy = accuracy_score(y_train, knn.predict(X_train)) # COMPLETAR
    ks_train_acc[indice] = train_accuracy # COMPLETAR

    # Evaluar accuracy en test y guardar
    test_accuracy = accuracy_score(y_test, knn.predict(X_test)) # COMPLETAR
    ks_test_acc[indice] = test_accuracy # COMPLETAR

    # Graficar regiones de decisión
    if k in [1,2,5,10,20,30]:
        indx += 1
        plt.subplot(2,3,indx)
        plt.title(f"KNN (k={k}) - Train Acc: {train_accuracy:.2f}, Test Acc: {test_accuracy:.2f}")
        xx, yy = np.meshgrid(np.linspace(X[:,0].min(), X[:,0].max(), 150), np.linspace(X[:,1].min(), X[:,1].max(), 150))
        Z = knn.predict(np.c_[xx.ravel(), yy.ravel()]).reshape(xx.shape)
        plt.contourf(xx, yy, Z, alpha=0.3)
        plt.scatter(X_train[:, 0], X_train[:, 1], s=50, marker='*', c=y_train,edgecolors='k', label='Puntos train')
        plt.scatter(X_test[:, 0], X_test[:, 1], c=y_test, edgecolors='k', label='Puntos test')
        plt.legend()
plt.tight_layout()
plt.show()

# Graficar curva k vs accuracy
plt.figure(figsize=(8,3))
plt.plot(ks,ks_train_acc, label='Accuracy train') 
plt.plot(ks,ks_test_acc, label='Accuracy test')  
plt.ylabel('Accuracy')
plt.xlabel('k (cantidad de vecinos)')
plt.legend()
plt.grid()
plt.show()

**EXPERIMENTAR:**

Investigar el parámetro $weights$ del clasificador. Cambiar el valor por defecto a _"distance"_ y observar si cambia la curva de accuracy. 


# Árboles de decisión

In [ ]:
from sklearn.tree import DecisionTreeClassifier
from utils import display_tree
import os
IMAGES_PATH = './P2_outputs'
# Crear carpeta con imágenes a guardar
if not os.path.exists(IMAGES_PATH):
    os.mkdir(IMAGES_PATH)

Generar datos para clasificar

In [ ]:
n_samples = 1000
# Generación de datos para clasificación
X, y = make_classification(n_samples=n_samples, n_features=2, n_informative=2, 
                           n_redundant=0, n_classes=4, n_clusters_per_class=1, 
                           random_state=42, weights=[0.4, 0.2, 0.15, 0.5])

# Visualizar conjunto de datos
plt.scatter(X[:, 0], X[:, 1], c=y, edgecolors='k')
plt.title('Espacio de características')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()

# Separar train y test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=41)

Entrenar un árbol de decisión sin restricciones

In [ ]:
tree = DecisionTreeClassifier(random_state=42)
tree.fit(X_train,y_train)

score_train = tree.score(X_train, y_train)
print('Aciertos train:',score_train)
score_test = tree.score(X_test, y_test)
print('Aciertos test: ',score_test)

# Desplegar forma del árbol
display_tree(tree, IMAGES_PATH, 'arbol.dot')

**PREGUNTAS:**

1. ¿Se da una situación de subajuste o sobreajuste? ¿Por qué?
1. ¿Qué profundidad tiene el árbol? (verificar con el método `get_depth()`)

Entrenar un árbol de decisión restringiendo la profundidad a 5 nodos

_Nota: investigar el hiperparámetro `max_depth` en [la documentación](https://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html)_

In [ ]:
tree_max_depth = DecisionTreeClassifier(max_depth=5) # COMPLETAR
tree_max_depth.fit(X_train,y_train)

score_train = tree_max_depth.score(X_train, y_train)
print('Aciertos train:',score_train)
score_test = tree_max_depth.score(X_test, y_test)
print('Aciertos test: ',score_test)

display_tree(tree_max_depth, IMAGES_PATH, 'arbol_max_depth.dot')

Entrenar un árbol de decisión restringiendo la cantidad de muestras por hoja. Que cada hoja tenga como mínimo 7 muestras.

In [ ]:
tree_min_samp = DecisionTreeClassifier(min_samples_leaf=7) # COMPLETAR
tree_min_samp.fit(X_train,y_train)

score_train = tree_min_samp.score(X_train, y_train)
print('Aciertos train:',score_train)
score_test = tree.score(X_test, y_test)
print('Aciertos test: ',score_test)

display_tree(tree_min_samp, IMAGES_PATH, 'arbol_min_samples_leaf.dot')

**RESPONDER:**

¿Cuál modelo tiene mejor desempeño? ¿Esto quiere decir que es mejor? 

Discutir si con estas evaluaciones es suficiente para decidir cuál es mejor.

_Respuesta:_

Completar la siguiente celda que utiliza _**valdación cruzada**_ sobre cada una de las opciones anteriores

In [ ]:
from sklearn.model_selection import cross_val_score
from utils import plot_classifier_regions

# Completar función para desplegar scores de validación cruzada
def display_cv_scores(clf, X, y, cv_num=10, scoring="accuracy", extra_string=None):
    """  
    Función que entrena un clasificador por validación cruzada e imprime
    la media y varianza en los conjuntos de validación.

    Entradas:
    - clf: clasificador de sklearn
    - X: conjunto de datos
    - y: etiquetas/valores ground-truth
    - cv_num (int) : cantidad de veces para hacer validación cruzada
    - scoring (str): string que indica qué score utilizar
    - extra_string (str): (opcional) string para desplegar que sirva para identificar el experimento hecho
    """
    
    scores = cross_val_score(clf, X, y, scoring=scoring, cv=cv_num) # COMPLETAR scores obtenidos con cross_val_score
    
    cv_mean = scores.mean() # COMPLERTAR media de scores
    cv_std = scores.std() # COMPLERTAR desviación estándar de scores

    print(f"CV Mean {extra_string}: {cv_mean:.3f}")
    print(f"CV Standard deviation {extra_string}: {cv_std:.3f}")


In [ ]:
cv_num = 10 # número de divisiones para validación cruzada

# Arbol sin restricciones
display_cv_scores(tree, X_train, y_train, cv_num=cv_num, extra_string='sin restricciones')
plot_classifier_regions(tree, 
                      X_train, y_train,
                      X_test, y_test
                      )
print('----------------------------------------')

# Arbol con máxima profundidad
display_cv_scores(tree_max_depth, X_train, y_train, cv_num=cv_num, extra_string='restringiendo profundidad')
plot_classifier_regions(tree_max_depth, 
                      X_train, y_train,
                      X_test, y_test
                      )
print('----------------------------------------')

# Arbol con mínima cantidad de muestras por hoja
display_cv_scores(tree_min_samp, X_train, y_train, cv_num=cv_num, extra_string='restringiendo muestras por hoja')
plot_classifier_regions(tree_min_samp, 
                      X_train, y_train,
                      X_test, y_test
                      )

**EXPERIMENTAR:**

Realizar el análisis de validación cruzada para otro hiperparámetro de árbol de decisión (ver sección _parameters_ de [la documentación](https://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html)). 

Discutir según los valores del sesgo y varianza. Desplegar la forma del árbol y graficar las regiones de decisión para éste último entrenamiento.